## Automation system for assigning relevant tags/keywords to Arabic news using NLP


## Problem statement
Online newspapers become very popular in the past decade. It replaced the classic newspaper since it is convenient and environment friendly. Moreover, news in online newspaper can be easily searched. So, it will be more efficient if we add tags to each news that reflect the news topic. In this work, I will work on Arabic news data-set and I will  add tags to each news based on TF-IDF weight of each word.

## Code

### Imports

In [39]:
import nltk
nltk.download('stopwords')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\baso0\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\baso0\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.


True

In [26]:
import pandas as pd
from nltk.corpus import stopwords
from string import punctuation 
import pandas as pd
import re
import numpy as np
from nltk.tokenize import word_tokenize
from nltk.stem.isri import ISRIStemmer
from nltk.tokenize.treebank import TreebankWordDetokenizer
import argparse
import time
from math import log
from math import sqrt
import string

### Load data and select the news text only 

In [27]:
ar_stp = pd.read_fwf('stop_words.txt', header=None)
fdata = pd.read_csv('news_data.csv')
fdata.shape

(4130, 11)

In [28]:
fdata = fdata.dropna(axis=0, subset=['news_text'])
fdata.shape

(4128, 11)

### Text pre-processing
* Remove stopwords
* Remove links, numbers, and punctuation
* Stemming _return the wort to its  root
* Tokenization

### Functions used in preprocessing 

In [29]:
def process_data(arr, stem=False, tokinzie=False, threshold=0):
    """
    takes an array of string/texts and remove stopwords, punctuation, and return the root of the word.

    Arguments: 
    arr: numpy array or list. texts to be cleaned.
    stem: boolean. True return the stme of the word, False keep the original.
    tokinzie: boolean. True return a tokinzie version of a text. False Return as text.
    threshold: int. set the threshold of lenght of text to keep.

    Returns:
    an array of cleaned text.  
    """
    print ('start', arr)
    missing_values = arr.isna().sum()
    if missing_values > 0:
        raise ValueError(f'found {missing_values} missing values')

    # if threshold > 0:
    #     arr = [item for item in arr if len(arr) > threshold]

    # processed_arr = [self.ـprocess_text(item, stem) for item in arr]
    print ('before get arabic words')

    processed_arr = _get_arabic_words(arr)
    print ('after get arabic words' , processed_arr)

    # for i, item in enumerate(processed_arr):
    #     print(len(item))

    if tokinzie:
        return processed_arr
    print ('after tokinize', processed_arr)

    # arr_detokenized = [TreebankWordDetokenizer().detokenize(word) for word in processed_arr]

    return processed_arr

In [67]:
def process_text(value, stem):
    print (value)

    value = re.sub('((www\.[^\s]+)|(https?://[^\s]+))', '', value) # remove URLs
    print ('remove URLs done')

    value = re.sub('@[^\s]+', '', value) # remove usernames
    print ('remove usernames done')

    # value = re.sub('[0-9]', '', value)
    value = re.sub('[a-zA-Z]', '', value)
    print ('remove numbers done')
    # value = re.sub(r'\d', '', value)
    value = re.sub('^[\u0621-\u064A\u0660-\u0669 ]+$', '', value) # remove special characters like ('\n') 
    print ('remove special characters done')
    value = re.sub(r'#([^\s]+)', r'\1', value) # remove the # in #hashtag
    print ('remove # done')
    value = re.sub(r'(.)\1+', r'\1', value)
    print ('remove unwanted charecters done')


    value = word_tokenize(value)
    print ('after  token ')
    

#     if stem:
    value = _stem(value)
    print ('after  stem ')

    return [word for word in value if word not in _stopWords] 

def _stem( arr):

    _st = ISRIStemmer()

    value = [_st.pre32(word) for word in arr] 
    value = [_st.suf32(word) for word in arr]
    # value = [_st.waw(word) for word in arr]
    value = [_st.stem(word) for word in arr]

    return value


In [47]:
def _remove_stopwords(arr):
    """"
    the purpose of this function is to remove stop words from a text
   
    Arguments:
    arr: List. of texts
    
    Returns:
    a List of text removed of stop words
    """
    ar_stp = pd.read_fwf('stop_words.txt', header=None)
    
    stop_words = set(stopwords.words('arabic') + list(ar_stp[0])) 
    #stop_words = list(ar_stp[0])

    return [word for word in arr if word not in stop_words]

In [58]:

def _get_arabic_words(arr):
    """
    the purpose of this function is to get arabic words only out of texts. 
    to be used in term frequncy - inverse - term frequency.
    takes an array of texts and return only arabic words
    Arguments:
    arr: Series. array of documents.
   
    
    Returns:
    a Series of arabic words per document
    """
    # remove (?, !, , ...)
    punctuation = string.punctuation  + '،'+'؛'+   '؟' +'ّ'
    arr = [sentence.translate(str.maketrans('', '', punctuation)) for sentence  in arr]
    print(" remove punc done ! ")
    # keep only arabic words  
    arr_text = [re.findall(r'[\u0600-\u06FF]+', sentence) for sentence in arr]
   
    
    arr_text = [_handle_char(item) for item in arr_text]
    print(" keep only arabic words done ! ")

    # remove stop words
    arr_text = [_remove_stopwords(text) for text in arr_text]
    print(" remove stop words done ! ")
    
    new_arr = []

    for text in arr_text:
        new_arr.append(' '.join(text))


    return pd.Series(new_arr)


In [59]:
def _handle_char(list):
    
    """
    takes a list of words represent a tweet and return words removed of repeated characters and irregular short words
    Arguments:
    arr: Series. array of tweets.
    
    Returns:
    a list of words removed of repeated characters ( e.g احببب: احب) and irregular short words
    """
    arr = [re.sub(r'(.)\1+', r'\1', word) for word in list]
    arr = [word for word in list if len(word) >= 3]
    return arr



#### I used an open source script for arabic language to apply these preproceessing steps

In [68]:
_stopWords = set(stopwords.words('arabic') + list(punctuation) + list(ar_stp[0]))
data = pd.DataFrame()
data ['news_text'] = fdata['news_text']
data['processed'] = process_data(data['news_text'], stem=False, tokinzie=False, threshold=0)


start 0       حذّرت الهيئة العامة للغذاء والدواء من منتج عسل...
1       أقامت حكومة مدينة يوكوهاما، والمعهد الوطني للد...
2       أظهر مقطع فيديو متداول آخر للفتاة المقيمة، وهي...
3       أنقذت شجاعة مواطن اليوم فريقًا لشركة متعاقدة م...
4       استقبل مدير الدفاع المدني بمنطقة الرياض، اللوا...
                              ...                        
4125    في مفاجأة كبيرة، أعلن عالم سابق في إدارة الطير...
4126    بحث عضو مجلس الإدارة رئيس لجنة تنمية الأعمال ب...
4127    أكّد الباحث في الطقس والمناخ عضو لجنة تسمية ال...
4128    ناقش مجلس الشورى، خلال جلسة العادية "62" من أع...
4129    عبَّر مصدر مسؤول بوزارة الخارجية عن إدانة المم...
Name: news_text, Length: 4128, dtype: object
before get arabic words
 remove punc done ! 
 keep only arabic words done ! 
 remove stop words done ! 
after get arabic words 0       حذرت الهيئة العامة للغذاء والدواء منتج عسل للع...
1       أقامت حكومة مدينة يوكوهاما والمعهد الوطني للدر...
2       أظهر مقطع فيديو متداول آخر للفتاة المقيمة وهي ...
3       أن

In [69]:
data.head(20)

news_text  \
0   حذّرت الهيئة العامة للغذاء والدواء من منتج عسل...   
1   أقامت حكومة مدينة يوكوهاما، والمعهد الوطني للد...   
2   أظهر مقطع فيديو متداول آخر للفتاة المقيمة، وهي...   
3   أنقذت شجاعة مواطن اليوم فريقًا لشركة متعاقدة م...   
4   استقبل مدير الدفاع المدني بمنطقة الرياض، اللوا...   
5   تحقق شرطة محافظة جدة في واقعة العثور على مقيم ...   
6   توقعت الهيئة العامة للأرصاد وحماية البيئة، ممث...   
7   أعلن المدير الفني للمنتخب السعودي الأول "رينار...   
8   نظم مستشفى الملك فيصل التخصصي ومركز الأبحاث با...   
9   كشف رئيس اللجنة العليا لمشروع قياس وتحقيق رضا ...   
10  أعلن صندوق تنمية الموارد البشرية (هدف)، بالشرا...   
11  سجَّل المركز الطبي التابع للهيئة الملكية بمدين...   
12  اشتكى طلاب مدرسة العطاء بضحى سيالة والتابعة لم...   
13  باشرت الفرق الإسعافية التابعة للهلال الأحمر ال...   
14  عبر مصدر مسؤول بوزارة الخارجية عن رفضه التام ل...   
15  هطلت ظهر اليوم، أمطار متوسطة إلى غزيرة على مدي...   
16  أعلنت إمارة منطقة مكة المكرمة، القبض على مواطن...   
17  وصل خادم الحرمين الشريفين إلى مقر مجلس الشورى ...   
18  بدأ مساء اليوم بيع تذاكر اعتزال ياسر القحطاني ...   
19   قال رئيس مجلس إدارة غرفة الرياض الأستاذ عجلان...   

                                            processed  
0   حذرت الهيئة العامة للغذاء والدواء منتج عسل للع...  
1   أقامت حكومة مدينة يوكوهاما والمعهد الوطني للدر...  
2   أظهر مقطع فيديو متداول آخر للفتاة المقيمة وهي ...  
3   أنقذت شجاعة مواطن اليوم فريقًا لشركة متعاقدة إ...  
4   استقبل مدير الدفاع المدني بمنطقة الرياض اللواء...  
5   تحقق شرطة محافظة جدة واقعة العثور مقيم الجنسية...  
6   توقعت الهيئة العامة للأرصاد وحماية البيئة ممثل...  
7   أعلن المدير الفني للمنتخب السعودي الأول رينارد...  
8   نظم مستشفى الملك فيصل التخصصي ومركز الأبحاث با...  
9   كشف رئيس اللجنة العليا لمشروع قياس وتحقيق رضا ...  
10  أعلن صندوق تنمية الموارد البشرية هدف بالشراكة ...  
11  سجَل المركز الطبي التابع للهيئة الملكية بمدينة...  
12  اشتكى طلاب مدرسة العطاء بضحى سيالة والتابعة لم...  
13  باشرت الفرق الإسعافية التابعة للهلال الأحمر ال...  
14  عبر مصدر مسؤول بوزارة الخارجية رفضه التام لتصر...  
15  هطلت ظهر اليوم أمطار متوسطة غزيرة مدينة سبت ال...  
16  أعلنت إمارة منطقة مكة المكرمة القبض مواطن ظهر ...  
17  وصل خادم الحرمين الشريفين مقر مجلس الشورى ليلق...  
18  بدأ مساء اليوم بيع تذاكر اعتزال ياسر القحطاني ...  
19  قال رئيس مجلس إدارة غرفة الرياض الأستاذ عجلان ...

### Add new column that contains the processed text

In [70]:
data['processed'] =data [data['processed'].notnull()]['processed'].apply(lambda col : process_text(col, True) )

حذرت الهيئة العامة للغذاء والدواء منتج عسل للعلامة التجارية العسل الصحي نظراً لاحتوائه مادة دوائية تستخدم بوصفة طبية وقالت الهيئة العسل الصحي تنتجه شركة ماليزيا يخالف اللائحة الفنية المعتمدة لعسل النحل رقم بسبب احتوائه المادة الدوائية تادالافيل تستخدم بموجب وصفة طبية وأوصت المستهلكين بتجنب المنتج والتخلص لديهم فوراً حفاظاً صحتهم مشيرة أنها تتابع تنفيذ الإجراءات للتأكد خلو الأسواق المنتج
remove URLs done
remove usernames done
remove numbers done
remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
أقامت حكومة مدينة يوكوهاما والمعهد الوطني للدراسات الإنسانية بجامعة اكيتا اليابانية ومؤسسة موتوكو كاتاكورا لثقافة الصحراء معرض استكشاف عامًا التراث الثقافي وادي فاطمة بمحافظة الجموم بمنطقة مكة المكرمة متحف يوكوهاما للثقافات الأوروبية الآسيوية بإشراف الهيئة العامة للسياحة والتراث الوطني السعودية وبتعاونٍ الملحقية الثقافية السعودية باليابان المعهد العربي الإسلامي ومكتب رابطة العالم الإسلامي اليابان وتزامنًا المعرض أُقيم المؤتمر الدولي الأول مستق

after  stem 
ناشد ذوو الشاب محمد سعدون الدوسري المساعدة البحث عنه بعدما فُقد قبل سنة وتسعة شهور خرج منزله بأحد أحياء الرياض معرفة وجهته ولم يعد الآن قالت والدته فقدت ابني محمد حينما خرج المنزل بحي الرمال وقت متأخر وقارب اليوم اختفائه سنة وتسعة شهور يعاني اعتلالات نفسية زلنا نعلم مصيره شيئًا الوقت الحالي وأفادت والدته بأنهم أبلغوا الجهات الأمنية ممثلة بشرطة الحمراء الرياض تاريخ فقدانه لكنهم يجدوا أثر مناشدين لديه معلومات تساعد العثور التواصل الرقم
remove URLs done
remove usernames done
remove numbers done
remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
أكد الباحث الطقس والمناخ عضو لجنة تسمية الحالات عبدالعزيز الحصيني انخفاضاً ملموساً لدرجات الحرارة سيستمر يوم السبت وقال عبر حسابه تويتر فجر اليوم الأربعاء نلاحظ تعمُق الكتلة الباردة معظم مناطق المملكة متوقع مزيد الانخفاض يصرفها الله ومتوقع استمرارها السبت الأحد ترجع كانت بإذن الله وأضاف محافظات الرياض والشرقية الجنوبية تأثرت بحالة غيث واليوم الأربعاء تأثير الحالة الأمارات وعُمان والر

remove unwanted charecters done
after  token 
after  stem 
أعرب مكتب الأمم المتحدة لحقوق الإنسان قلقه الشديد اليوم الثلاثاء استخدام قوات الأمن الإيرانية الذخيرة الحية المتظاهرين مطالباً السلطات بالحد استخدام القوة لتفريق الاحتجاجات أطلقت شرارتها زيادة أسعار الوقود جهته دعا المتحدث باسم المكتب روبرت كولفيل السلطات إيران إعادة خدمة الإنترنت المقطوعة السبت الماضي واحترام المتظاهرين حرية التعبير والتجمع السلمي بحسب أوردت رويترز أفاد كولفيل إفادة بجنيف بأن المكتب وصلته تقارير عدد القتلى مظاهرات إيران بالعشرات وحذر المتحدث حجم الضحايا خطير للغاية واضح
remove URLs done
remove usernames done
remove numbers done
remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
بتوجيه أمير المنطقة الشرقية الأمير سعود نايف عبدالعزيز أعلنت بلدية القطيف تمديد فعاليات مهرجان الزهور الأول بالمحافظة السبت المقبل نظراً للإقبال الكبير والحضور الكثيف لفعاليات الملتقى وكانت بلدية محافظة القطيف أطلقت مهرجان الزهور الأول بمحافظة القطيف يوم الخميس الماضي وبلغت عدد شتلات 

remove usernames done
remove numbers done
remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
تفاعلت جامعة القرى بمكة المكرمة مقطع فيديو الفئران الميتة وتراكم النفايات سطح أحد المعامل بإحدى الكليات بالجامعة وأعلنت تنظيف وتعقيم المكان جاء تفاعلاً ساعة نشر سبق خبرًا تحت عنوان شاهد فئران ميتة تستوطن سطح إحدى كليات جامعة القرى وبه الفيديو وثَقه طالب وزود سبق وأكد المتحدث باسم جامعة القرى الدكتور عثمان قزاز الجامعة قامت بالوقوف المكان المشار إليه وتم تنظيفه وتعقيمه وكان مقطع فيديو وثَقه طالب بجامعة القرى بمكة المكرمة أظهر تراكم النفايات وانتشار الفئران الميتة سطح أحد المعامل وداخل غرفة شكل مستودع بإحدى الكليات بالجامعة يُنذر بكارثة بيئية وصحية وبحسب الطالب المكان يقع الدور الثالث مبنى الكلية ومرتبط بشكل مباشر المصعد الكهربائي للكلية يعني الوصول إليه سهل ومتاح طريق المصعد إغلاق المكان وتنظيفه قِبل الجهة المسؤولة وأظهر المقطع فئرانًا ميتة ومخلفات ونفايات تعود لأحد المعامل يُعتقد أنه الاستغناء والتخلص بهذه الطريقة العشوائية وسط مطالبات موثق ا

remove # done
remove unwanted charecters done
after  token 
after  stem 
نشبت اشتباكات قوات الأمن ومتظاهرين شيراز نقلت وسائل إعلام محلية أنباء إغلاق مدارس مدينة إيرانية اليوم الاثنين بسبب الاحتجاجات وفقًا لموقع قناة العربية وتفصيلاً لقي شخصًا مصرعهم احتجاجات إيران حسبما أورده أمس الأحد راديو فردا الناطق بالفارسية ظهرت مواقع التواصل الاجتماعي مقاطع فيديو لتظاهرات حاشدة عبادان بالأحواز وأعلنت المعارضة الإيرانية وقت سابق سقوط قتيلاً الاحتجاجات تشهدها البلاد أفادت مصادر لقناتَيْ العربية والحدث بأن قوات الأمن الإيرانية أطلقت أمس الأحد قنابل الغاز لتفريق المحتجين ميدان الخميني طهران وامتدت الاحتجاجات معظم المدن الإيرانية تحت سُمي انتفاضة البنزين وأشارت وكالة فارس اعتقال متظاهر إيران خلال يومَيْن وسط أنباء وقوع قتلى صفوف المتظاهرين خلال احتجاجات أمس وعلى وقع التصعيد أفادت وكالة مهر بمصادقة مجلس الأمن القومي الإيراني مشروع قانون تقنين استهلاك الوقود ودعا البرلمان جلسة مغلقة اتخاذ الإجراءات اللازمة للسيطرة والإشراف أسعار البنزين يتضرر الشعب بحسب وكالة مهر للأنباء وازدادت وتيرة الاحتجاجات وعمت م

...

remove usernames done
remove numbers done
remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
قامت رائدتا الفضاء ناسا كريستينا كوك وجيسيكا مير بأول مهمة سير نسائية الفضاء عملتا خارج محطة الفضاء الدولية لتبديل شاحن بطارية مكسور المثير الأمر مكاناً الأرض لفت انتباه إحداهما ارتفاع آلاف الأميال ووصفته بـمكان رائع اتضح وفق مقطع فيديو نشرته شبكة الإخبارية الأمريكية أنهما كانتا تقصدان موقعاً بُعد كيلومتر جنوب العاصمة السعودية الرياض وكانت صنعت رائدتا الفضاء الأمريكيتان كريستينا كوتش وجيسيكا مير التاريخ الجمعة عندما خرجتا محطة الفضاء الدولية أول سير الفضاء نسائي بالكامل علق الرئيس الأمريكي دونالد ترامب الحدث التاريخي وتحقق الحدث طال انتظاره لإدارة الطيران والفضاء الأمريكية ناسا خلال مهمة روتينية نسبياً لاستبدال بطاريات معطلة السطح الخارجي للمحطة وأعلنت ناسا مقطع مصور مباشر للعملية كوتش ومير خرجتا بالملابس البيضاء المحطة الواقعة ارتفاع كيلومترات فوق الأرض الفضاء الخارجي الساعة صباحاً بتوقيت شرق الولايات المتحدة بتوقيت غرينتش لاستبدال وحدة طاقة

remove URLs done
remove usernames done
remove numbers done
remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
أكد الكاتب السعودي صحيفة الأنباء الكويتية منصور الضبعان الواجب كبير المنظمات والفرق التطوعية والقطاع الخاص والحكومة يتعلق بإحصاء المتسولين والذهاب وتوفير فرص عمل ووظائف عادية انتظار لأي مبادرة منهم وقال الضبعان الخطأ انتظار المشرد المتسول المعدم ينهض ويبحث عمل كان يملك أدوات الحياة عاش هامشها وحذر الضبعان خطر المتسولين مبديًا استغرابه الجميع يراهم الجهات المعنية وأضاف مقاله السبعيني الروسي فيشسلاف راسنر وبعد سنوات العيش مشردًا منزل تحول لأحد أشهر المرشدين السياحيين لمعالم ثاني أكبر مدينة روسيا سان بطرسبورغ وأردف القصة الملهمة تجوب العالمالمتبقي فقط استنباط الفوائد واستخراج العوائد واستلهام العبر وتابع مدينة مدن العالم تجد المسحوقين يدفقون ماء الوجه غالبيتهم خطر يحتمل وفي الخليج باب أولى والغريب الجميع يراهم الجهات المعنية وقال الضبعان راسنر يقول للعالم الحل موجود ولكنه نقص القادرين التمام تنتظر المشرد المتسول المعدم ينهض ويبح

remove numbers done
remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
اجتمع أفضل الطهاة العرب أرض مركز الملك عبدالعزيز الثقافي العالمي إثراء ضمن أجواء موسم تنوين للإبداع نسخته الثانية تستمر فعالياته مدى يوماً سيقدم الطهاة مزيدًا العروض أكتوبر الجاري جانبها أوضحت الشيف السعودي صالح خلال تقديمها فعالية الـتوب شيف إثراء كأحد فعاليات وأنشطة موسم تنوين الثاني الأفكار لتطوير الأكلات الشعبية السعودية قائمة كونها جزءًا أصيلًا الثقافة السائدة ولاسيما قرب انطلاق أكاديميات حكومية ومعاهد لفن الطهي السعودي والإتيكيت وأضافت صالح أنه الاتفاق مؤخرًا هيئات حكومية لإنشاء معاهد لفن الطهي والإتيكيت تخص المطبخ السعودي خلال العام المقبل وذلك تقديم رؤية ومقترحات بهذا الصدد التجربة التلفزيونية خاضتها مشددة أهمية تدريس أصول المطبخ السعودي يكتنزه نكهات مميزة معمول الدول الأخرى وقالت سأقدم الكبسة بالطريقة الصينية وسيتناول زوار إثراء الكبسة بالأعواد قدمتها أخيرًا السفارة السعودية بالصين أنها قدمت مؤتمر بجنوب أفريقيا طبق السليق السعودي بطريقة غريبة استهوت جميع 

remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
قادت الدكتورة إكرام بليلو أستاذ علم النبات جامعة الملك عبدالله للعلوم والتقنية فريقًا بحثيًا لجمع عينات أشجار النخيل القديمة مزرعة الضابطة التاريخية بجوار مسجد قباء المدينة المنورة وفي التفاصيل قالت الدكتورة إكرام يوجد العالم نوع أشجار النخيل نوع فقط المملكة مضيفة لأن هدفنا الأساس تحسين إنتاج وجودة تمور النخيل المملكة فقد قررنا التركيز تمور عجوة المدينة نظرًا لقيمتها الاجتماعية والدينية البلاد جاء تزامنًا يوم الأغذية العالمي بدأ فريق علماء النبات جامعة الملك عبدالله للعلوم والتقنية كاوست مشروعًا بحثيًا كبيرًا وواعدًا يهدف لتحسين إنتاج التمور وحماية أشجار النخيل العالم يعد المشروع الأول نوعه يتم دراسة جينوم نخيل التمر بشكل شامل وسبق نُشر للدكتورة إكرام بليلو دراسة متميزة العام بالمجلة العلمية تشرح تتمكن النباتات الصحراوية النمو والازدهار الظروف البيئية القاسية والصعبة كالجفاف والحرارة وفي سياق الدراسة نفسها تطور فرق البحث التابعة لمركز الزراعة الصحراوية كاوست أدوات وتقنيات لتحسين زراع

remove # done
remove unwanted charecters done
after  token 
after  stem 
انتقد رئيس الاستخبارات السابق الأمير تركي الفيصل الرئيس الأمريكي دونالد ترامب بسبب قرار الانسحاب سوريا مؤكداً أنه قرار حكيم وقال الفيصل لقاء بالعربية الرئيس الأمريكي ترامب غرابة تعبيره الأشياء وفيما يتعلق بانتشار قوات أمريكية السعودية قال كان الإيرانيون يريدون إحداث اضطرابات فالمملكة وحلفاؤها استعداد لذلك كانوا يريدون يتعاونوا وأن يكونوا شركاء بناء تحقيق السلام والأمن فقط الخليج المنطقة كلها حولنا فهناك مجالٌ للمناقشة وبحسب سبوتنيك عربي بدأت الولايات المتحدة يوم الإثنين الماضي سحب قواتها منطقة شمال شرق سوريا قرب الحدود تركيا قيام الأخيرة بعملية عسكرية لتطهير الأراضي وحدات حماية الشعب الكردية تنشط ضمن تحالف قوات سوريا الديمقراطية المدعوم أمريكياً الحرب داعش وتعدها أنقرة تنظيماً إرهابياً وذراعاً حزب العمال الكردستاني
remove URLs done
remove usernames done
remove numbers done
remove special characters done
remove # done
remove unwanted charecters done
after  token 
after  stem 
أثارت تصريحات النائب اللبناني ماريو عون

In [71]:
data.head()

news_text  \
0  حذّرت الهيئة العامة للغذاء والدواء من منتج عسل...   
1  أقامت حكومة مدينة يوكوهاما، والمعهد الوطني للد...   
2  أظهر مقطع فيديو متداول آخر للفتاة المقيمة، وهي...   
3  أنقذت شجاعة مواطن اليوم فريقًا لشركة متعاقدة م...   
4  استقبل مدير الدفاع المدني بمنطقة الرياض، اللوا...   

                                           processed  
0  [حذر, هيئ, عمة, غذء, دوء, نتج, عسل, علم, جرة, ...  
1  [قمت, حكم, دين, وكو, عهد, وطن, درس, سان, جمع, ...  
2  [ظهر, قطع, يدو, داول, اخر, لفت, قيم, وهي, حدث,...  
3  [قذت, شجع, وطن, اليوم, فرق, لشر, عاقد, حدى, اد...  
4  [قبل, دير, دفع, دني, نطق, ريض, واء, خلد, حرق, ...

### Remove null values 

In [72]:
data = data.dropna(axis=0, subset=['processed'])

data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4126 entries, 0 to 4127
Data columns (total 2 columns):
news_text    4126 non-null object
processed    4126 non-null object
dtypes: object(2)
memory usage: 96.7+ KB


### Extract all words appeared in all documents

In [73]:
total_terms = []
for p in data['processed']:
    #print (p)
    total_terms = total_terms + p

total_terms = list(set(total_terms))
print ("len " , len (total_terms))
TF_table = pd.DataFrame()
#TF_table['doc'] = data['processed']


len  13529


In [74]:
total_terms

['وجث',
 'فتأ',
 'نوح',
 'بصص',
 'لاستهدفت',
 '٥١٤',
 'كضبط',
 'كأيقو',
 'رنج',
 'شطب',
 'ذئب',
 'قبة',
 'واستكمال',
 'حجو',
 'رنبرغ',
 'ترض',
 'روبرتو',
 'بتصريحاته',
 'وخم',
 'متف',
 'سهد',
 'عون',
 'أخمد',
 'زدك',
 'بشا',
 'ميكانيكا',
 'رأت',
 'يجب',
 'فهي',
 'ظرف',
 'جهض',
 'ومعاقبته',
 'مضي',
 'لعي',
 'فيل',
 'حيط',
 'مالامبو',
 'فصل',
 'اجب',
 'يذؤ',
 'صفه',
 'صيدلانية',
 'ائه',
 'موه',
 'حيض',
 'زرع',
 'جبي',
 'وغم',
 'بحو',
 'مغناطيسي',
 'لفك',
 'اعق',
 'هايلوكس',
 'ويم',
 'بودوسيروس',
 'مترولوجي',
 'باراغواي',
 'صح',
 'ومقتنياته',
 'ؤده',
 'وإسبانية',
 'كورتيس',
 'طنةعم',
 'جده',
 'بنب',
 'يكي',
 'فنـ',
 'أعرب',
 'لرش',
 'ولمستشفى',
 'كأحد',
 'مالديف',
 'أسج',
 'غلى',
 'تبغ',
 'تسغ',
 'جحم',
 'موزمبيق',
 'سيخ',
 'واستبعاد',
 'اوعقائدية',
 'حاسيس',
 'أكراد',
 'لذي',
 'نبع',
 'بيت',
 'كربط',
 'اقف',
 'استغرابه',
 'فعت',
 'كند',
 'أخرج',
 'إنجاح',
 'نافيجيتور',
 'بطي',
 'شمي',
 'صرخ',
 'كأنماط',
 'أجيال',
 'بذل',
 'انطلاقته',
 'لمساعدته',
 'مشـاريع',
 'قرش',
 'اسماعيلي',
 'حلی',


### Calculate term frequency TF for all words for each document

In [75]:
TF_table['doc'] = data['processed']
for t in total_terms:
    tff = []
    for d in TF_table['doc']:
        ff = str(d).count(t)
        #tf(t,str(d))
        tff.append(ff)
    TF_table[t]=tff

In [76]:
export_csv = TF_table.to_csv (r'TF_table.csv', index = None, header=True) 

In [78]:
TF_table = pd.read_csv('TF_table.csv')

In [79]:
TF_table.shape

(4126, 13530)

### Clean the new data by removing any term that doesnt appear in any of the documents

In [80]:
TF_table = TF_table.loc[:, (TF_table != 0).any(axis=0)]

In [81]:
TF_table.shape

(4126, 13527)

### Add the text to the new data frame

In [82]:
TF_table['doc'] = data['processed']
TF_table.columns

Index(['doc', 'وجث', 'فتأ', 'نوح', 'بصص', 'لاستهدفت', '٥١٤', 'كضبط', 'كأيقو',
       'رنج',
       ...
       'ريسنج', 'نحق', 'طلو', 'رولاند', 'وتناولته', 'ميزونياكي', 'نبض', 'دنس',
       'سذج', 'غيت'],
      dtype='object', length=13527)

### Calculate the document frequency DF for each term

In [83]:
df = {'doc':'df'}
for t in TF_table.columns[1:]:
    df[t] = TF_table[t].astype(bool).sum(axis=0)

In [84]:
len(df)

13527

In [85]:
uniqueValues = set(df.values())
fz = {value:key for key, value in df.items()}


### Calculate TF-IDF for each term for each document

In [86]:
numDocumentsWithThisTerm = TF_table.loc[TF_table['doc'] == 'df']

idf = {}
count = 1
for t in TF_table.columns[1:]:
    n = TF_table.shape [0]  
    d = float(TF_table.astype(bool).sum(axis=0)[count])
    cc = n/d
    print ("d" , d)
    idf[t] = round(log(float(cc),2),3)
    count = count +1


d 2.0
d 4.0
d 17.0
d 3.0
d 1.0
d 2.0
d 1.0
d 1.0
d 5.0
d 8.0
d 4.0
d 7.0
d 31.0
d 5.0
d 1.0
d 4.0
d 2.0
d 1.0
d 8.0
d 5.0
d 2.0
d 78.0
d 2.0
d 1.0
d 6.0
d 4.0
d 19.0
d 367.0
d 57.0
d 124.0
d 2.0
d 2.0
d 33.0
d 7.0
d 62.0
d 229.0
d 1.0
d 770.0
d 28.0
d 1.0
d 6.0
d 6.0
d 14.0
d 5.0
d 3.0
d 184.0
d 4.0
d 1.0
d 1.0
d 10.0
d 3.0
d 4.0
d 3.0
d 91.0
d 1.0
d 1.0
d 2.0
d 1545.0
d 2.0
d 2.0
d 1.0
d 1.0
d 3.0
d 5.0
d 10.0
d 43.0
d 1.0
d 120.0
d 3.0
d 1.0
d 18.0
d 3.0
d 3.0
d 10.0
d 11.0
d 1.0
d 2.0
d 1.0
d 1.0
d 1.0
d 1.0
d 3.0
d 2.0
d 48.0
d 95.0
d 118.0
d 1.0
d 2.0
d 2.0
d 1.0
d 41.0
d 4.0
d 24.0
d 1.0
d 1.0
d 4.0
d 62.0
d 1.0
d 13.0
d 317.0
d 11.0
d 5.0
d 2.0
d 21.0
d 2.0
d 2.0
d 11.0
d 3.0
d 15.0
d 50.0
d 94.0
d 16.0
d 4.0
d 5.0
d 1.0
d 53.0
d 6.0
d 1.0
d 4.0
d 1.0
d 43.0
d 12.0
d 329.0
d 40.0
d 1.0
d 8.0
d 1.0
d 78.0
d 23.0
d 8.0
d 1.0
d 792.0
d 2.0
d 6.0
d 1.0
d 1.0
d 25.0
d 4.0
d 15.0
d 8.0
d 1.0
d 4.0
d 41.0
d 28.0
d 11.0
d 2.0
d 1.0
d 24.0
d 1.0
d 6.0
d 2.0
d 1.0
d 1.0
d 51.0
d 8.0
d 393

d 1.0
d 393.0
d 13.0
d 60.0
d 1.0
d 29.0
d 2.0
d 1.0
d 5.0
d 7.0
d 9.0
d 1004.0
d 2.0
d 3.0
d 848.0
d 1.0
d 135.0
d 2.0
d 3.0
d 2.0
d 1.0
d 8.0
d 10.0
d 56.0
d 5.0
d 19.0
d 5.0
d 6.0
d 1.0
d 1.0
d 3.0
d 2.0
d 17.0
d 1.0
d 204.0
d 1.0
d 180.0
d 25.0
d 2.0
d 23.0
d 49.0
d 4.0
d 9.0
d 419.0
d 1.0
d 2.0
d 1.0
d 1.0
d 10.0
d 7.0
d 10.0
d 2.0
d 7.0
d 10.0
d 421.0
d 2.0
d 13.0
d 1.0
d 1.0
d 8.0
d 109.0
d 21.0
d 86.0
d 4.0
d 1.0
d 10.0
d 24.0
d 22.0
d 1.0
d 11.0
d 1.0
d 30.0
d 1.0
d 8.0
d 1.0
d 1.0
d 3.0
d 10.0
d 46.0
d 27.0
d 1.0
d 2.0
d 1.0
d 2.0
d 3.0
d 31.0
d 10.0
d 2.0
d 1.0
d 15.0
d 1.0
d 1.0
d 1.0
d 1.0
d 2.0
d 1.0
d 53.0
d 2.0
d 673.0
d 1.0
d 69.0
d 7.0
d 1.0
d 1.0
d 4.0
d 47.0
d 3.0
d 42.0
d 17.0
d 11.0
d 2.0
d 1.0
d 2.0
d 13.0
d 55.0
d 3.0
d 2.0
d 33.0
d 1.0
d 1.0
d 71.0
d 1.0
d 1.0
d 6.0
d 8.0
d 88.0
d 4.0
d 1.0
d 1.0
d 1638.0
d 39.0
d 3.0
d 1.0
d 92.0
d 15.0
d 1.0
d 5.0
d 136.0
d 22.0
d 1.0
d 1.0
d 35.0
d 10.0
d 2046.0
d 1.0
d 1.0
d 62.0
d 16.0
d 15.0
d 3.0
d 862.0
d 260.0
d 19.0
d

d 1.0
d 1.0
d 6.0
d 66.0
d 2.0
d 1.0
d 72.0
d 5.0
d 8.0
d 12.0
d 5.0
d 5.0
d 2.0
d 2.0
d 1.0
d 4.0
d 15.0
d 3.0
d 1.0
d 1.0
d 1.0
d 54.0
d 1.0
d 1.0
d 1.0
d 1.0
d 1.0
d 1.0
d 1.0
d 24.0
d 2.0
d 53.0
d 1.0
d 1.0
d 1.0
d 318.0
d 406.0
d 48.0
d 5.0
d 9.0
d 1.0
d 1.0
d 1.0
d 2.0
d 8.0
d 1.0
d 11.0
d 63.0
d 2.0
d 1.0
d 62.0
d 5.0
d 1.0
d 2.0
d 2.0
d 25.0
d 3.0
d 20.0
d 1.0
d 3.0
d 1.0
d 2.0
d 5.0
d 5.0
d 2.0
d 9.0
d 1.0
d 1.0
d 23.0
d 1.0
d 60.0
d 188.0
d 15.0
d 2.0
d 1.0
d 63.0
d 3.0
d 1.0
d 16.0
d 2.0
d 32.0
d 2.0
d 2.0
d 1.0
d 20.0
d 1.0
d 1.0
d 3.0
d 7.0
d 1.0
d 52.0
d 2.0
d 2.0
d 1.0
d 4.0
d 4.0
d 7.0
d 28.0
d 1.0
d 2.0
d 243.0
d 4.0
d 1.0
d 1.0
d 2.0
d 3.0
d 2.0
d 1.0
d 2.0
d 1.0
d 1.0
d 2.0
d 5.0
d 5.0
d 1.0
d 1.0
d 13.0
d 11.0
d 260.0
d 1.0
d 671.0
d 226.0
d 54.0
d 1.0
d 1.0
d 53.0
d 6.0
d 3.0
d 1062.0
d 17.0
d 1.0
d 1.0
d 35.0
d 4.0
d 5.0
d 83.0
d 67.0
d 1.0
d 15.0
d 8.0
d 353.0
d 4.0
d 1.0
d 1.0
d 2944.0
d 4.0
d 2.0
d 1.0
d 1.0
d 168.0
d 1.0
d 1.0
d 1.0
d 76.0
d 1.0
d 18.0
d 1.0
d

d 18.0
d 3.0
d 27.0
d 1053.0
d 11.0
d 25.0
d 7.0
d 60.0
d 1.0
d 40.0
d 9.0
d 30.0
d 22.0
d 1.0
d 24.0
d 4.0
d 24.0
d 14.0
d 2.0
d 1.0
d 1.0
d 78.0
d 1.0
d 17.0
d 1.0
d 19.0
d 1.0
d 35.0
d 1.0
d 121.0
d 1.0
d 1.0
d 545.0
d 1.0
d 13.0
d 10.0
d 21.0
d 33.0
d 29.0
d 10.0
d 22.0
d 1.0
d 1.0
d 1.0
d 19.0
d 2.0
d 2.0
d 2.0
d 481.0
d 5.0
d 6.0
d 3.0
d 29.0
d 14.0
d 31.0
d 65.0
d 29.0
d 3.0
d 2.0
d 1.0
d 13.0
d 11.0
d 1.0
d 90.0
d 1.0
d 2.0
d 1.0
d 1.0
d 1.0
d 11.0
d 8.0
d 1.0
d 1.0
d 2.0
d 7.0
d 19.0
d 2.0
d 1.0
d 15.0
d 1.0
d 2.0
d 25.0
d 17.0
d 1.0
d 3.0
d 3.0
d 5.0
d 2.0
d 1.0
d 1.0
d 1.0
d 61.0
d 6.0
d 219.0
d 37.0
d 5.0
d 2.0
d 2.0
d 39.0
d 1.0
d 1.0
d 1.0
d 15.0
d 21.0
d 246.0
d 35.0
d 1.0
d 1.0
d 4.0
d 1.0
d 2.0
d 2.0
d 1.0
d 1.0
d 1.0
d 1.0
d 3.0
d 21.0
d 1.0
d 6.0
d 6.0
d 3.0
d 1.0
d 1.0
d 2.0
d 5.0
d 4.0
d 1.0
d 4.0
d 7.0
d 13.0
d 21.0
d 3.0
d 1.0
d 44.0
d 1.0
d 3.0
d 1.0
d 8.0
d 3.0
d 1.0
d 1.0
d 24.0
d 6.0
d 7.0
d 3.0
d 24.0
d 1.0
d 3.0
d 9.0
d 52.0
d 1.0
d 310.0
d 1.0
d 1.0
d 1.0


d 11.0
d 2.0
d 1.0
d 23.0
d 3.0
d 22.0
d 14.0
d 1.0
d 1.0
d 9.0
d 2.0
d 15.0
d 298.0
d 1.0
d 1.0
d 16.0
d 6.0
d 215.0
d 5.0
d 6.0
d 7.0
d 110.0
d 1.0
d 2.0
d 150.0
d 67.0
d 40.0
d 10.0
d 14.0
d 3.0
d 5.0
d 1.0
d 22.0
d 3.0
d 1.0
d 2.0
d 54.0
d 4.0
d 25.0
d 14.0
d 1.0
d 1.0
d 54.0
d 1.0
d 1.0
d 1.0
d 2.0
d 9.0
d 2.0
d 1.0
d 65.0
d 1677.0
d 6.0
d 1.0
d 12.0
d 1.0
d 3.0
d 1.0
d 1.0
d 4.0
d 17.0
d 4.0
d 84.0
d 22.0
d 6.0
d 1.0
d 36.0
d 40.0
d 1.0
d 138.0
d 1.0
d 268.0
d 10.0
d 1.0
d 1.0
d 2.0
d 48.0
d 1.0
d 4.0
d 1.0
d 2.0
d 37.0
d 1.0
d 1.0
d 20.0
d 31.0
d 5.0
d 216.0
d 101.0
d 1.0
d 1.0
d 888.0
d 170.0
d 252.0
d 4.0
d 2.0
d 1.0
d 7.0
d 3.0
d 2.0
d 4.0
d 8.0
d 1.0
d 24.0
d 11.0
d 193.0
d 17.0
d 28.0
d 121.0
d 57.0
d 1.0
d 7.0
d 1.0
d 1.0
d 3.0
d 1.0
d 8.0
d 12.0
d 20.0
d 70.0
d 10.0
d 40.0
d 14.0
d 5.0
d 4.0
d 1.0
d 1.0
d 12.0
d 2.0
d 1.0
d 1.0
d 6.0
d 1144.0
d 1.0
d 2.0
d 3.0
d 57.0
d 17.0
d 1.0
d 43.0
d 1.0
d 1.0
d 1.0
d 6.0
d 5.0
d 1.0
d 2.0
d 1.0
d 1.0
d 69.0
d 20.0
d 37.0
d 1.0
d 1.0

...

d 4.0
d 10.0
d 3.0
d 1.0
d 9.0
d 186.0
d 2.0
d 1.0
d 1.0
d 3.0
d 710.0
d 3.0
d 2.0
d 1.0
d 2.0
d 15.0
d 1.0
d 17.0
d 5.0
d 8.0
d 93.0
d 1.0
d 4.0
d 1.0
d 1.0
d 54.0
d 16.0
d 8.0
d 1.0
d 23.0
d 2.0
d 1.0
d 4.0
d 3.0
d 1.0
d 27.0
d 2.0
d 12.0
d 2.0
d 3.0
d 3.0
d 1.0
d 6.0
d 1.0
d 53.0
d 1.0
d 28.0
d 38.0
d 1.0
d 130.0
d 2.0
d 2.0
d 1.0
d 1.0
d 72.0
d 480.0
d 1.0
d 1.0
d 1.0
d 4.0
d 1.0
d 1.0
d 2.0
d 1.0
d 1.0
d 1.0
d 1.0
d 3.0
d 3.0
d 1.0
d 1.0
d 15.0
d 10.0
d 4.0
d 1.0
d 131.0
d 1.0
d 3.0
d 11.0
d 1.0
d 1.0
d 20.0
d 2.0
d 23.0
d 3.0
d 3.0
d 12.0
d 78.0
d 1.0
d 19.0
d 967.0
d 1.0
d 9.0
d 1.0
d 1.0
d 277.0
d 4.0
d 1.0
d 1.0
d 1.0
d 7.0
d 31.0
d 22.0
d 484.0
d 9.0
d 16.0
d 1.0
d 10.0
d 183.0
d 4.0
d 1.0
d 1.0
d 103.0
d 11.0
d 10.0
d 1.0
d 1.0
d 48.0
d 1.0
d 26.0
d 5.0
d 100.0
d 6.0
d 3.0
d 30.0
d 10.0
d 1.0
d 1.0
d 2.0
d 21.0
d 6.0
d 3.0
d 12.0
d 1.0
d 1.0
d 344.0
d 284.0
d 2.0
d 3.0
d 1.0
d 2.0
d 1051.0
d 198.0
d 72.0
d 4.0
d 1.0
d 454.0
d 2.0
d 1.0
d 58.0
d 4.0
d 432.0
d 132.0
d 10.0
d 1

d 11.0
d 3.0
d 102.0
d 2.0
d 3.0
d 8.0
d 20.0
d 4.0
d 15.0
d 1.0
d 1.0
d 6.0
d 1.0
d 8.0
d 681.0
d 321.0
d 418.0
d 1.0
d 1.0
d 6.0
d 6.0
d 15.0
d 1.0
d 4.0
d 21.0
d 1.0
d 2.0
d 6.0
d 4.0
d 28.0
d 50.0
d 118.0
d 2.0
d 1.0
d 1.0
d 65.0
d 2.0
d 17.0
d 2.0
d 7.0
d 2.0
d 2.0
d 7.0
d 3.0
d 1.0
d 4.0
d 56.0
d 4.0
d 1.0
d 147.0
d 4.0
d 1.0
d 15.0
d 2.0
d 1.0
d 455.0
d 8.0
d 16.0
d 90.0
d 1.0
d 11.0
d 1.0
d 37.0
d 21.0
d 49.0
d 4.0
d 2.0
d 2.0
d 4.0
d 2.0
d 1.0
d 1.0
d 92.0
d 1.0
d 4.0
d 107.0
d 72.0
d 1.0
d 2.0
d 1.0
d 11.0
d 5.0
d 2.0
d 1.0
d 32.0
d 1.0
d 1.0
d 29.0
d 4.0
d 1.0
d 2.0
d 2.0
d 1.0
d 62.0
d 1333.0
d 1.0
d 1.0
d 1.0
d 1.0
d 1.0
d 6.0
d 7.0
d 54.0
d 1.0
d 3.0
d 31.0
d 1.0
d 1.0
d 75.0
d 1.0
d 48.0
d 1.0
d 1.0
d 334.0
d 1.0
d 3.0
d 5.0
d 1.0
d 1.0
d 3.0
d 1.0
d 15.0
d 11.0
d 1.0
d 2.0
d 1.0
d 1.0
d 41.0
d 1.0
d 1.0
d 15.0
d 5.0
d 4.0
d 1.0
d 1.0
d 1.0
d 1.0
d 1.0
d 1.0
d 350.0
d 1.0
d 6.0
d 1.0
d 3.0
d 27.0
d 13.0
d 59.0
d 4.0
d 1.0
d 4.0
d 2.0
d 8.0
d 1.0
d 24.0
d 2.0
d 82.0
d 149

d 3.0
d 1.0
d 127.0
d 2.0
d 177.0
d 1.0
d 997.0
d 8.0
d 1.0
d 10.0
d 1.0
d 1.0
d 6.0
d 2.0
d 1.0
d 4.0
d 1.0
d 38.0
d 1.0
d 50.0
d 7.0
d 315.0
d 2.0
d 3.0
d 1.0
d 1.0
d 2.0
d 4.0
d 1.0
d 33.0
d 25.0
d 12.0
d 1.0
d 3.0
d 1.0
d 1.0
d 12.0
d 31.0
d 2.0
d 1.0
d 26.0
d 1.0
d 2.0
d 5.0
d 4.0
d 1.0
d 1.0
d 1.0
d 1.0
d 2.0
d 24.0
d 90.0
d 2.0
d 1.0
d 44.0
d 108.0
d 20.0
d 2.0
d 7.0
d 1.0
d 203.0
d 67.0
d 60.0
d 1.0
d 112.0
d 6.0
d 8.0
d 1.0
d 1.0
d 54.0
d 2.0
d 6.0
d 3.0
d 36.0
d 1.0
d 958.0
d 31.0
d 1.0
d 1.0
d 15.0
d 646.0
d 40.0
d 1.0
d 2.0
d 69.0
d 26.0
d 1.0
d 1.0
d 1.0
d 1.0
d 188.0
d 32.0
d 1.0
d 4.0
d 1.0
d 1.0
d 1.0
d 11.0
d 8.0
d 1.0
d 9.0
d 1.0
d 1.0
d 1.0
d 135.0
d 5.0
d 26.0
d 1.0
d 1.0
d 1.0
d 1.0
d 2.0
d 2.0
d 1.0
d 1.0
d 13.0
d 7.0
d 79.0
d 1.0
d 2.0
d 1.0
d 1.0
d 9.0
d 18.0
d 3.0
d 2.0
d 4.0
d 1.0
d 1.0
d 36.0
d 520.0
d 1.0
d 1.0
d 40.0
d 4.0
d 1.0
d 32.0
d 30.0
d 10.0
d 3.0
d 1.0
d 56.0
d 48.0
d 4.0
d 2.0
d 25.0
d 1.0
d 6.0
d 149.0
d 1.0
d 9.0
d 27.0
d 6.0
d 1.0
d 1.0
d 1.0
d

d 1.0
d 1.0
d 1.0
d 1.0
d 6.0
d 3.0
d 35.0
d 144.0
d 46.0
d 10.0
d 139.0
d 1.0
d 3.0
d 1.0
d 1.0
d 1.0
d 1.0
d 13.0
d 2.0
d 1557.0
d 22.0
d 25.0
d 1.0
d 18.0
d 2.0
d 7.0
d 11.0
d 13.0
d 9.0
d 1.0
d 11.0
d 2.0
d 1.0
d 25.0
d 25.0
d 88.0
d 7.0
d 21.0
d 7.0
d 87.0
d 1.0
d 39.0
d 1.0
d 39.0
d 19.0
d 31.0
d 21.0
d 30.0
d 134.0
d 391.0
d 51.0
d 1.0
d 1.0
d 1.0
d 1.0
d 1.0
d 20.0
d 1.0
d 3.0
d 9.0
d 4.0
d 5.0
d 57.0
d 2.0
d 20.0
d 234.0
d 10.0
d 24.0
d 1.0
d 1.0
d 3.0
d 2.0
d 1.0
d 1.0
d 8.0
d 4.0
d 3.0
d 1.0
d 1.0
d 10.0
d 1.0
d 1.0
d 11.0
d 9.0
d 1.0
d 128.0
d 1.0
d 3.0
d 14.0
d 3.0
d 9.0
d 1.0
d 2.0
d 1.0
d 2.0
d 19.0
d 1.0
d 15.0
d 2.0
d 3.0
d 61.0
d 35.0
d 5.0
d 1.0
d 1575.0
d 1.0
d 1.0
d 4.0
d 1.0
d 17.0
d 82.0
d 1.0
d 456.0
d 1.0
d 19.0
d 5.0
d 1.0
d 996.0
d 71.0
d 2.0
d 1.0
d 594.0
d 14.0
d 1.0
d 3.0
d 29.0
d 3.0
d 2.0
d 1.0
d 2.0
d 1.0
d 27.0
d 2.0
d 1.0
d 1.0
d 89.0
d 25.0
d 117.0
d 4.0
d 1.0
d 13.0
d 71.0
d 18.0
d 1.0
d 4.0
d 6.0
d 3.0
d 1.0
d 2.0
d 1.0
d 100.0
d 58.0
d 17.0
d 3.0


d 9.0
d 196.0
d 1.0
d 2.0
d 8.0
d 882.0
d 3.0
d 1.0
d 2.0
d 191.0
d 23.0
d 2.0
d 18.0
d 1.0
d 2.0
d 150.0
d 3.0
d 4.0
d 1.0
d 9.0
d 8.0
d 1.0
d 3.0
d 2.0
d 65.0
d 7.0
d 1.0
d 1.0
d 751.0
d 7.0
d 1.0
d 32.0
d 1.0
d 8.0
d 2.0
d 4.0
d 1.0
d 21.0
d 7.0
d 1.0
d 3.0
d 1.0
d 1.0
d 2.0
d 2.0
d 107.0
d 141.0
d 5.0
d 2.0
d 12.0
d 1.0
d 43.0
d 13.0
d 7.0
d 1.0
d 2.0
d 7.0
d 1.0
d 241.0
d 2.0
d 1.0
d 16.0
d 5.0
d 3.0
d 22.0
d 2.0
d 4.0
d 45.0
d 1.0
d 49.0
d 30.0
d 5.0
d 3.0
d 1.0
d 1.0
d 93.0
d 4.0
d 234.0
d 7.0
d 33.0
d 4.0
d 6.0
d 1.0
d 1.0
d 1.0
d 430.0
d 1.0
d 7.0
d 43.0
d 193.0
d 3.0
d 97.0
d 1.0
d 1.0
d 1.0
d 1.0
d 18.0
d 1.0
d 1.0
d 3.0
d 157.0
d 1.0
d 1.0
d 1.0
d 12.0
d 9.0
d 243.0
d 33.0
d 1.0
d 5.0
d 1.0
d 1.0
d 1.0
d 7.0
d 2.0
d 9.0
d 16.0
d 1.0
d 2.0
d 6.0
d 1.0
d 1.0
d 1.0
d 1.0
d 9.0
d 13.0
d 630.0
d 25.0
d 8.0
d 117.0
d 2.0
d 27.0
d 4.0
d 197.0
d 105.0
d 1.0
d 14.0
d 51.0
d 3.0
d 1.0
d 19.0
d 5.0
d 4.0
d 56.0
d 5.0
d 15.0
d 11.0
d 1.0
d 1.0
d 231.0
d 1.0
d 23.0
d 3.0
d 1.0
d 8.0
d 4

In [87]:
TFIDF = pd.DataFrame()
TFIDF = TF_table

In [88]:
for f in TFIDF.columns[1:]:
    TFIDF[f] =  TFIDF[f].apply(lambda col : float(col) * idf[f])

In [89]:
export_csv = TFIDF.to_csv (r'TFIDF2.csv', index = None, header=True) 

In [90]:
TFIDF= TFIDF.drop( columns='doc')

In [91]:
TFIDF.head()

وجث  فتأ  نوح  بصص  لاستهدفت  ٥١٤  كضبط  كأيقو  رنج  شطب  ...  ريسنج  نحق  \
0  0.0  0.0  0.0  0.0       0.0  0.0   0.0    0.0  0.0  0.0  ...    0.0  0.0   
1  0.0  0.0  0.0  0.0       0.0  0.0   0.0    0.0  0.0  0.0  ...    0.0  0.0   
2  0.0  0.0  0.0  0.0       0.0  0.0   0.0    0.0  0.0  0.0  ...    0.0  0.0   
3  0.0  0.0  0.0  0.0       0.0  0.0   0.0    0.0  0.0  0.0  ...    0.0  0.0   
4  0.0  0.0  0.0  0.0       0.0  0.0   0.0    0.0  0.0  0.0  ...    0.0  0.0   

   طلو  رولاند  وتناولته  ميزونياكي  نبض  دنس  سذج  غيت  
0  0.0     0.0       0.0        0.0  0.0  0.0  0.0  0.0  
1  0.0     0.0       0.0        0.0  0.0  0.0  0.0  0.0  
2  0.0     0.0       0.0        0.0  0.0  0.0  0.0  0.0  
3  0.0     0.0       0.0        0.0  0.0  0.0  0.0  0.0  
4  0.0     0.0       0.0        0.0  0.0  0.0  0.0  0.0  

[5 rows x 13526 columns]

In [92]:
temp = TFIDF.transpose()

In [93]:
temp.head()

0     1     2     3     4     5     6     7     8     9     ...  \
وجث        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
فتأ        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
نوح        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
بصص        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
لاستهدفت   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   

          4118  4119  4120  4121  4122  4123  4124  4125  4126  4127  
وجث        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
فتأ        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
نوح        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
بصص        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
لاستهدفت   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  

[5 rows x 4126 columns]

### For each document, select the terms with highest TFIDF value to be the tag

In [94]:
tags = []
for t in temp.columns[1:]:
    x= temp.nlargest(5,t)
    tags.append(x)

In [95]:
newtag = []
for d in tags:
    t = str(d.index)
    e = t.find('dtype')-2
    newtag.append(t[6:e])

In [96]:
Tags = pd.DataFrame()
Tags['tags'] = newtag

In [97]:
Tags['orig'] = data['news_text']

In [98]:
Tags.head()

tags  \
0  ['ياب', 'ثقف', 'وكو', 'موتوكو', 'توك']   
1  ['كورنيش', 'نيش', 'رني', 'ورن', 'ندم']   
2   ['ـشيول', 'شيو', 'بحة', 'يول', 'سيل']   
3     ['دير', 'حرق', 'واء', 'هلل', 'حمر']   
4     ['توفى', 'عثر', 'وفى', 'جث', 'يدن']   

                                                orig  
0  حذّرت الهيئة العامة للغذاء والدواء من منتج عسل...  
1  أقامت حكومة مدينة يوكوهاما، والمعهد الوطني للد...  
2  أظهر مقطع فيديو متداول آخر للفتاة المقيمة، وهي...  
3  أنقذت شجاعة مواطن اليوم فريقًا لشركة متعاقدة م...  
4  استقبل مدير الدفاع المدني بمنطقة الرياض، اللوا...

In [99]:
export_csv = Tags.to_csv (r'NewsTags.csv', index = None, header=True) 

## Conclusion
In this project I worked on Arabic news data-set to add tags as new feature. The worst challenge that I faced during this project was the long running time issue. As future work, I intend to repeat the experiment without stemming and compare the results. Moreover, this work can be a good foundation for developing simple search engine.   